# Lanes Processing

Previously, we generated maps that showed how much cyclable trips there were in each district (choropleth maps).

Now, we want to discover the number of trips that passes through each street of the city (based on the routes generated with GraphHopper API)

This notebook process each São Paulo lane and compares with the OD trips to get the number of trips that passes there.

The files resulting from this processing are in the `bases\Potential_V2` and `bases\Bycicle_Trips_Per_lane` folders. 

If you already have these files, you can skip this notebook's execution (that may take **dozens** of hours).

In [1]:
%load_ext autoreload
%autoreload 2
import saopaulo.load_trips as sptr
import saopaulo.maps_aux as aux
import saopaulo.cycling_infrastructure as cinfra
import saopaulo.choropleth as spchoro

from shapely.geometry import LineString, Point
#import saopaulo.choropleth_folium as spchoro

import saopaulo.sp_grid as gr

from bikescience.intersect_ways import geometry_intersection_length

import geopandas as gpd
import json
import pandas as pd
import numpy as np
from ipywidgets import interact_manual, widgets, fixed
from IPython.core.display import display, HTML, clear_output
import folium

import warnings
import requests
import os
import fnmatch as fnm
warnings.simplefilter('ignore')

gr.SP_LAT = -23.63
gr.SP_LON = -46.55


/home/pedro/.local/lib/python3.8/site-packages/geopandas/_compat.py:106: UserWarning: The Shapely GEOS version (3.8.0-CAPI-1.13.1 ) is incompatible with the GEOS version PyGEOS was compiled with (3.9.0-CAPI-1.16.2). Conversions between both will be slow.
  warnings.warn(


In [2]:
districts_name = [
    'Bela Vista', 'Bom Retiro', 'Cambuci', 'Consolação', 'Liberdade', 
    'República', 'Santa Cecília', 'Sé','Butantã', 'Morumbi', 'Raposo Tavares', 
    'Rio Pequeno', 'Vila Sônia', 'Barra Funda', 'Jaguara', 'Jaguaré', 'Lapa', 
    'Perdizes', 'Vila Leopoldina', 'Alto de Pinheiros', 'Itaim Bibi', 
    'Jardim Paulista', 'Pinheiros','Aricanduva', 'Carrão', 'Vila Formosa',
    'Água Rasa', 'Belém', 'Brás', 'Mooca', 'Pari', 'Tatuapé', 'Artur Alvim',
    'Cangaíba', 'Penha', 'Vila Matilde', 'São Lucas', 'Sapopemba',
    'Vila Prudente','Cidade Tiradentes', 'Ermelino Matarazzo', 'Ponte Rasa',
    'Guaianases', 'Lajeado', 'Itaim Paulista', 'Vila Curuçá', 'Cidade Líder',
    'Itaquera', 'José Bonifácio', 'Parque do Carmo', 'Iguatemi', 'São Mateus',
    'São Rafael', 'Jardim Helena', 'São Miguel', 'Vila Jacuí','Cachoeirinha', 
    'Casa Verde', 'Limão', 'Brasilândia', 'Freguesia do Ó', 'Anhanguera', 
    'Perus', 'Jaraguá', 'Pirituba', 'São Domingos','Jaçanã', 'Tremembé', 
    'Mandaqui', 'Santana', 'Tucuruvi', 'Vila Guilherme', 'Vila Maria', 
    'Vila Medeiros','Cursino', 'Ipiranga', 'Sacomã', 'Jabaquara', 'Moema', 
    'Saúde', 'Vila Mariana', 'Campo Limpo', 'Capão Redondo', 'Vila Andrade', 
    'Cidade Dutra', 'Grajaú', 'Socorro', 'Cidade Ademar', 'Pedreira', 
    'Jardim Ângela', 'Jardim São Luís', 'Marsilac', 'Parelheiros',
    'Campo Belo', 'Campo Grande', 'Santo Amaro']

In [3]:
#read data

districts = True
OD_zone = !districts 

if districts:
    zone_shp = gpd.read_file('../data/sao-paulo/od/shapes/Distritos_2017_region.shp')
    zone_shp.crs = {'init': 'epsg:31983'}  
    zone_shp.to_crs(epsg='4326', inplace=True)
    # converting to km^2
    zone_shp['Area_ha_2'] = zone_shp['Area_ha'] / 100
    zone_shp['NumeroZona'] = zone_shp['NumeroDist']
    zone_shp['NomeZona'] = zone_shp['NomeDistri']
    zone_shp['NumeroMuni'] = 0

    numeroMuni = []
    for _, d in zone_shp.iterrows():
        if d['NomeDistri'] in districts_name:
            numeroMuni.append(36)
        else:
            numeroMuni.append(0)
    zone_shp['NumeroMuni'] = numeroMuni
    
else:
    zone_shp = gpd.read_file('../data/sao-paulo/od/shapes/Zonas_2017_region.shp')
    zone_shp.crs = {'init': 'epsg:31983'}  
    zone_shp.to_crs(epsg='4326', inplace=True)

display(zone_shp)

# read routes files and join with general trips file
od_trips = pd.read_csv('bases/complete_csv.csv')
od_trips['final_potential_v2'] = (od_trips['inclination_potential'] + od_trips['distance_potential']) / 2
# fix FE_VIA with wrong format (because of thousand separator)
od_trips.loc[od_trips['FE_VIA'] >= 10000, 'FE_VIA'] = od_trips.loc[od_trips['FE_VIA'] >= 10000, 'FE_VIA'] / 1000

#od_trips.set_index('ID_ORDEM', inplace=True, drop=False)

od_trips.dropna(inplace = True)
od_trips = gpd.GeoDataFrame(od_trips, crs={'init': 'epsg:4326'},
                 geometry=[LineString(eval(r)) for r in od_trips['route']])

the_grid = gr.create(n=9, west_offset=-0.15, east_offset=0.23, north_offset=0.19, south_offset=-0.46)

NumeroDist              NomeDistri   Area_ha  \
0             1               Água Rasa    715.05   
1             2       Alto de Pinheiros    751.26   
2             3              Anhanguera   3339.95   
3             4              Aricanduva    686.26   
4             5             Artur Alvim    653.04   
..          ...                     ...       ...   
129         130      São Caetano do Sul   1536.53   
130         131   São Lourenço da Serra  18674.34   
131         132                  Suzano  20666.94   
132         133         Taboão da Serra   2043.37   
133         134  Vargem Grande Paulista   4257.94   

                                              geometry  Area_ha_2  NumeroZona  \
0    POLYGON ((-46.55380 -23.56843, -46.55387 -23.5...     7.1505           1   
1    POLYGON ((-46.69209 -23.54631, -46.69257 -23.5...     7.5126           2   
2    POLYGON ((-46.76082 -23.42733, -46.76088 -23.4...    33.3995           3   
3    POLYGON ((-46.50153 -23.57941, -46.50154 -23.5...     6.8626           4   
4    POLYGON ((-46.47300 -23.54029, -46.47302 -23.5...     6.5304           5   
..                                                 ...        ...         ...   
129  POLYGON ((-46.58317 -23.64088, -46.58326 -23.6...    15.3653         130   
130  POLYGON ((-46.98852 -23.79984, -46.98847 -23.7...   186.7434         131   
131  POLYGON ((-46.38321 -23.61775, -46.38318 -23.6...   206.6694         132   
132  POLYGON ((-46.81819 -23.63701, -46.82138 -23.6...    20.4337         133   
133  POLYGON ((-46.99444 -23.67076, -46.99479 -23.6...    42.5794         134   

                   NomeZona  NumeroMuni  
0                 Água Rasa          36  
1         Alto de Pinheiros          36  
2                Anhanguera          36  
3                Aricanduva          36  
4               Artur Alvim          36  
..                      ...         ...  
129      São Caetano do Sul           0  
130   São Lourenço da Serra           0  
131                  Suzano           0  
132         Taboão da Serra           0  
133  Vargem Grande Paulista           0  

[134 rows x 8 columns]

In [4]:
# used to generate the lanes_with_zones file
def calculate_lanes_district():
    progress = 0
    start_zones = []
    end_zones = []
    
    limit = len(lanes)
    for l in range(limit):
        if l / limit >= progress:
            print ((round(progress * 100))/2, '%')
            progress += 0.1
        lane = lanes.iloc[l]['geometry']
        for z in range(len(zone_shp)):
            zone = zone_shp.iloc[z]['geometry']
            p = lane.coords[0]
            if (Point(p[0], p[1]).within(zone)):
                start_zones.append(z)
                break
    progress = 0
    for l in range(limit):
        if l / limit >= progress:
            print (50 + (round(progress * 100)/2), '%')
            progress += 0.1
        lane = lanes.iloc[l]['geometry']
        for z in range(len(zone_shp)):
            zone = zone_shp.iloc[z]['geometry']
            p = lane.coords[-1]
            if (Point(p[0], p[1]).within(zone)):
                end_zones.append(z)
                break
    print(len(end_zones))
    print(len(lanes))

    # detects lanes that failed for some reason
    
    #x = 227726#round(len(start_zones) / 2)
    #print('start_zones[' + str(x - 1) + ']: ' + str(start_zones[x - 1]))
    #print('start_zones[' + str(x + 1) + ']: ' + str(start_zones[x + 1]))
    #print('----')
    #print('start_zones[' + str(x) + ']: ' + str(start_zones[x]))


    #lane = lanes.iloc[x]['geometry']
    #for z in range(len(zone_shp)):
    #    zone = zone_shp.iloc[z]['geometry']
    #    p = lane.coords[0]
    #    if (Point(p[0], p[1]).within(zone)):
    #        print('start zone [' + str(x) + ']: ' + str(z))
    #        break

    xs = [59527, 62146, 62809, 117922, 122213, 167759, 182608, 204117, 205273, 227724, 227726]   
    for x in xs:
        start_zones.append(0)
        start_zones[x + 1:] = start_zones[x:-1]       
    lanes['end_zone'] = end_zones      
    lanes['start_zone'] = start_zones
    lanes.to_file('lanes_with_zones.shp')
    

In [5]:
# detects the districts of the lanes
try:
    lanes = gpd.read_file('./bases/lanes_with_zones/lanes_with_zones.shp')

except:
    print('Processed file not found - loading original file')
    lanes = \
           gpd.read_file('../data/sao-paulo/geosampa/SIRGAS_SHP_logradouronbl/SIRGAS_SHP_logradouronbl.shp')
    lanes.crs = {'init': 'epsg:31983'}  
    lanes.to_crs(epsg='4326', inplace=True)
    
    print('Initiate processing')
    calculate_lanes_district()

In [6]:
# showing lanes of specific district (just to validate it visually)

fmap = gr.map_around_sp(the_grid=None,zoom=10,plot_grid=False)
folium.GeoJson(lanes.loc[pd.to_numeric(lanes['start_zone']) == 11], style_function = lambda x : {'color': 'black', 'weight': 2, 'opacity': 1, 'fillColor': 'black'},
                   name='ruas', control=False).add_to(fmap)

display(fmap)

In [7]:
display(od_trips)
display(type(od_trips))

display(od_trips)
display(type(od_trips))

orig_lat   orig_lon   dest_lat   dest_lon  \
0      -23.551678 -46.628858 -23.551495 -46.635115   
1      -23.551495 -46.635115 -23.551678 -46.628858   
2      -23.551678 -46.628858 -23.571829 -46.690238   
3      -23.571829 -46.690238 -23.525949 -46.666559   
4      -23.525949 -46.666559 -23.537903 -46.670921   
...           ...        ...        ...        ...   
175076 -23.401886 -47.008661 -23.402259 -47.009811   
175077 -23.393870 -47.003570 -23.398719 -47.002822   
175078 -23.398719 -47.002822 -23.393870 -47.003570   
175079 -23.393870 -47.003570 -23.398775 -47.001962   
175080 -23.398775 -47.001962 -23.393870 -47.003570   

                                                    route   ZONA  MUNI_DOM  \
0       [[-46.628827, -23.55186, 748.52], [-46.627845,...    1.0      36.0   
1       [[-46.635147, -23.551546, 783.14], [-46.635381...    1.0      36.0   
2       [[-46.628827, -23.55186, 748.52], [-46.627845,...    1.0      36.0   
3       [[-46.690264, -23.571842, 742.26], [-46.691246...    1.0      36.0   
4       [[-46.666835, -23.525929, 733.11], [-46.666934...    1.0      36.0   
...                                                   ...    ...       ...   
175076  [[-47.008662, -23.401916, 698.15], [-47.008789...  517.0      25.0   
175077  [[-47.00353, -23.393732, 699.83], [-47.00367, ...  517.0      25.0   
175078  [[-47.002834, -23.398807, 679.54], [-47.002995...  517.0      25.0   
175079  [[-47.00353, -23.393732, 699.83], [-47.00367, ...  517.0      25.0   
175080  [[-47.002039, -23.398937, 688.23], [-47.002223...  517.0      25.0   

        CO_DOM_X   CO_DOM_Y     ID_DOM  ...  ID_ORDEM       length  \
0       333743.0  7394463.0    10001.0  ...       1.0  1849.286293   
1       333743.0  7394463.0    10001.0  ...       2.0  1760.427711   
2       333743.0  7394463.0    10001.0  ...       3.0  9473.535456   
3       333743.0  7394463.0    10001.0  ...       4.0  6428.546731   
4       333743.0  7394463.0    10001.0  ...       4.0  2667.571706   
...          ...        ...        ...  ...       ...          ...   
175076  294618.0  7410518.0  5171418.0  ...  183088.0   131.295991   
175077  295243.0  7411456.0  5171599.0  ...  183089.0   816.655729   
175078  295243.0  7411456.0  5171599.0  ...  183090.0   752.109085   
175079  295243.0  7411456.0  5171599.0  ...  183091.0   897.452917   
175080  295243.0  7411456.0  5171599.0  ...  183092.0   832.906273   

             modal        id  distance_potential  age_potential  \
0       pedestrian       1.0            0.650491       0.023107   
1       pedestrian       2.0            0.689523       0.023107   
2           subway       3.0            0.032389       0.848482   
3           subway       4.0            0.077287       0.848482   
4           bus_sp       4.0            0.391186       0.848482   
...            ...       ...                 ...            ...   
175076  pedestrian  183088.0            0.128145       0.323018   
175077  pedestrian  183089.0            0.905531       0.720850   
175078  pedestrian  183090.0            0.826529       0.720850   
175079  pedestrian  183091.0            0.812320       0.980961   
175080  pedestrian  183092.0            0.767010       0.980961   

        inclination_potential  final_potential  final_potential_v2  \
0                    0.206501         0.293366            0.428496   
1                    0.463706         0.392112            0.576615   
2                    0.066909         0.315927            0.049649   
3                    0.402769         0.442846            0.240028   
4                    0.280026         0.506565            0.335606   
...                       ...              ...                 ...   
175076               0.843343         0.431502            0.485744   
175077               0.638682         0.755021            0.772107   
175078               0.441549         0.662976            0.634039   
175079               0.673910         0.822397            0.743115   
175080 

geopandas.geodataframe.GeoDataFrame

orig_lat   orig_lon   dest_lat   dest_lon  \
0      -23.551678 -46.628858 -23.551495 -46.635115   
1      -23.551495 -46.635115 -23.551678 -46.628858   
2      -23.551678 -46.628858 -23.571829 -46.690238   
3      -23.571829 -46.690238 -23.525949 -46.666559   
4      -23.525949 -46.666559 -23.537903 -46.670921   
...           ...        ...        ...        ...   
175076 -23.401886 -47.008661 -23.402259 -47.009811   
175077 -23.393870 -47.003570 -23.398719 -47.002822   
175078 -23.398719 -47.002822 -23.393870 -47.003570   
175079 -23.393870 -47.003570 -23.398775 -47.001962   
175080 -23.398775 -47.001962 -23.393870 -47.003570   

                                                    route   ZONA  MUNI_DOM  \
0       [[-46.628827, -23.55186, 748.52], [-46.627845,...    1.0      36.0   
1       [[-46.635147, -23.551546, 783.14], [-46.635381...    1.0      36.0   
2       [[-46.628827, -23.55186, 748.52], [-46.627845,...    1.0      36.0   
3       [[-46.690264, -23.571842, 742.26], [-46.691246...    1.0      36.0   
4       [[-46.666835, -23.525929, 733.11], [-46.666934...    1.0      36.0   
...                                                   ...    ...       ...   
175076  [[-47.008662, -23.401916, 698.15], [-47.008789...  517.0      25.0   
175077  [[-47.00353, -23.393732, 699.83], [-47.00367, ...  517.0      25.0   
175078  [[-47.002834, -23.398807, 679.54], [-47.002995...  517.0      25.0   
175079  [[-47.00353, -23.393732, 699.83], [-47.00367, ...  517.0      25.0   
175080  [[-47.002039, -23.398937, 688.23], [-47.002223...  517.0      25.0   

        CO_DOM_X   CO_DOM_Y     ID_DOM  ...  ID_ORDEM       length  \
0       333743.0  7394463.0    10001.0  ...       1.0  1849.286293   
1       333743.0  7394463.0    10001.0  ...       2.0  1760.427711   
2       333743.0  7394463.0    10001.0  ...       3.0  9473.535456   
3       333743.0  7394463.0    10001.0  ...       4.0  6428.546731   
4       333743.0  7394463.0    10001.0  ...       4.0  2667.571706   
...          ...        ...        ...  ...       ...          ...   
175076  294618.0  7410518.0  5171418.0  ...  183088.0   131.295991   
175077  295243.0  7411456.0  5171599.0  ...  183089.0   816.655729   
175078  295243.0  7411456.0  5171599.0  ...  183090.0   752.109085   
175079  295243.0  7411456.0  5171599.0  ...  183091.0   897.452917   
175080  295243.0  7411456.0  5171599.0  ...  183092.0   832.906273   

             modal        id  distance_potential  age_potential  \
0       pedestrian       1.0            0.650491       0.023107   
1       pedestrian       2.0            0.689523       0.023107   
2           subway       3.0            0.032389       0.848482   
3           subway       4.0            0.077287       0.848482   
4           bus_sp       4.0            0.391186       0.848482   
...            ...       ...                 ...            ...   
175076  pedestrian  183088.0            0.128145       0.323018   
175077  pedestrian  183089.0            0.905531       0.720850   
175078  pedestrian  183090.0            0.826529       0.720850   
175079  pedestrian  183091.0            0.812320       0.980961   
175080  pedestrian  183092.0            0.767010       0.980961   

        inclination_potential  final_potential  final_potential_v2  \
0                    0.206501         0.293366            0.428496   
1                    0.463706         0.392112            0.576615   
2                    0.066909         0.315927            0.049649   
3                    0.402769         0.442846            0.240028   
4                    0.280026         0.506565            0.335606   
...                       ...              ...                 ...   
175076               0.843343         0.431502            0.485744   
175077               0.638682         0.755021            0.772107   
175078               0.441549         0.662976            0.634039   
175079               0.673910         0.822397            0.743115   
175080 

geopandas.geodataframe.GeoDataFrame

In [8]:
fmap = gr.map_around_sp(the_grid=None,zoom=10,plot_grid=False)
folium.GeoJson(lanes.loc[lanes['start_zone'] == 11], style_function = lambda x : {'color': 'black', 'weight': 0.5, 'opacity': 1, 'fillColor': 'black'},
                   name='ruas', control=False).add_to(fmap)
folium.GeoJson(od_trips.iloc[range(4679, 4680)], style_function = lambda x : {'color': 'blue', 'weight': 2, 'opacity': 1, 'fillColor': 'black'},
                       control=False).add_to(fmap)

display(fmap)

In [9]:
#detects intersection between lanes and trips

example_trips = od_trips.iloc[4679]['geometry']
example_lanes = (lanes.loc[lanes['start_zone'] == 11])

example_lanes['potential_trips'] = 0
distances = []
intersects = []
for l in range(len(example_lanes)):
    lane = example_lanes.iloc[l]['geometry']
    #intersects.append((lane.intersects(example_trips)))
    distances.append(lane.distance(example_trips))
    intersects.append(lane.distance(example_trips) < 0.0005)
    
fmap = gr.map_around_sp(the_grid=None,zoom=10,plot_grid=False)
folium.GeoJson(example_lanes, style_function = lambda x : {'color': 'black', 'weight': 0.5, 'opacity': 1, 'fillColor': 'black'},
                   name='ruas', control=False).add_to(fmap)
folium.GeoJson(example_lanes.loc[intersects], style_function = lambda x : {'color': 'red', 'weight': 5, 'opacity': 1, 'fillColor': 'black'},
                   name='ruas', control=False).add_to(fmap)
folium.GeoJson(od_trips.iloc[range(4679, 4680)], style_function = lambda x : {'color': 'blue', 'weight': 2, 'opacity': 1, 'fillColor': 'black'},
                       control=False).add_to(fmap)

display(fmap)

In [10]:
import datetime
def trips_per_lane(trips, lanes, expansion = 'FE_VIA'):
    expansions = trips[expansion]
    trips_lane = [0]*len(lanes)
    progress = 0
    for l in range(len(lanes)):
        
        if l / len(lanes) >= progress:
            print (round(progress * 100), '%  - ', datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
            progress += 0.2
        
        lane = lanes.iloc[l]['geometry']
        for t in range(len(trips)):
            trip = trips.iloc[t]['geometry']
            if (lane.distance(trip) < 0.0005):
                trips_lane[l] += expansions.iloc[t]
    return trips_lane  

def trips_in_district(trips, district):
    is_in_district = []
    for i, t in trips.iterrows():
        is_in_district.append(district.intersects(t['geometry']))
        
    return trips.iloc[is_in_district]

def plot_potential_lanes(trips, lanes, district_name):
    district = zone_shp.loc[zone_shp['NomeDistri'] == district_name].convex_hull.scale(1.3, 1.3).iloc[0]
    trips = trips_in_district (trips, district)
    if len(trips) == 0:
        print('Sem viagens')
        return [0]*len(lanes)
        
    return trips_per_lane(trips, lanes)
    #lanes.to_file('PotentialV2_' + modal + '/potential_lanes_' + modal + '_' + district_name + '.shp')

In [11]:
# expands districts area (convex hull) to ensure all lanes were considered
# (because the processing will occur by district)

butanta = zone_shp.loc[zone_shp['NomeDistri'] == 'Butantã'].iloc[0]
butanta_scale = zone_shp.loc[zone_shp['NomeDistri'] == 'Butantã'].convex_hull.scale(1.3, 1.3).iloc[0]

fmap = gr.map_around_sp(the_grid=None,zoom=10,plot_grid=False) 
folium.GeoJson(butanta['geometry']).add_to(fmap)
folium.GeoJson(butanta_scale).add_to(fmap)
               
display(fmap)

#print(butanta['geometry'].geom_type)
#print('-------')
#print(trips_teste.convex_hull.geom_type)

#print(trips_teste.distance(butanta['geometry']))

teste = trips_in_district(od_trips, butanta_scale)
print(len(teste))

13791


In [12]:
# HARD PROCESSING
# MAY TAKE SEVERAL DAYS
# (thats why we do it by districts - so that it have "checkpoints")

def process_lanes_per_district():
    modals = od_trips.modal.unique()

    for i, zone in zone_shp.iterrows():

        #if (zone['NomeDistri'] not in ['Vila Andrade', 'Vila Curuçá', 'Vila Formosa']):
        #    continue
        print('******************************')
        print(zone['NomeDistri'])
        lanes_zone = lanes.loc[lanes['start_zone'] == zone['NumeroDist'] - 1]

        for modal in modals:
            print('------', modal)
            for quartil in range(4):
                print('---------- quartil', quartil)
                try:

                    trips = od_trips.loc[od_trips['final_potential_v2'] > quartil * .25]
                    trips = trips.loc[od_trips['final_potential_v2'] <= (quartil + 1) * .25]
                    trips = trips.loc[od_trips['modal'] == modal]

                    lanes_trips = plot_potential_lanes(
                        trips, lanes_zone,
                        zone['NomeDistri'])

                    lanes_zone['potential_trips_' + modal + '_' + str(quartil)] = lanes_trips

                except Exception as inst:
                    print(inst)    

        lanes_zone.to_file('bases/Potential_V2/potential_lanes_' + zone['NomeDistri'] + '.shp')
        
# process_lanes_per_district()

In [14]:
# do the same processing for bike tips
# may take a few hours

bike_trips = gpd.read_file('../data/sao-paulo/od/routes/bike_routes_in_sp.shp')
bike_trips.crs = {'init': 'epsg:4326'}
bike_trips['length'] = bike_trips['geometry'].length * 100000

for i, zone in zone_shp.iterrows():
    print(zone['NomeDistri'])
    
    lanes_zone = lanes.loc[lanes['start_zone'] == zone['NumeroDist'] - 1]

    
    lanes_trips = plot_potential_lanes(bike_trips, 
                         lanes.loc[lanes['start_zone'] == zone['NumeroDist'] - 1], 
                         zone['NomeDistri'])

    lanes_zone['bicycle_trips'] = lanes_trips
    
    lanes_zone.to_file('./bases/Bicycle_Trips_Per_Lane/bike_trips_per_lanes_' + zone['NomeDistri'] + '.shp')

Água Rasa
0 %  -  2023-03-07 16:17:18
20 %  -  2023-03-07 16:17:22
40 %  -  2023-03-07 16:17:25
60 %  -  2023-03-07 16:17:29
80 %  -  2023-03-07 16:17:32
Alto de Pinheiros
0 %  -  2023-03-07 16:17:36
20 %  -  2023-03-07 16:17:50
40 %  -  2023-03-07 16:18:07
60 %  -  2023-03-07 16:18:23
80 %  -  2023-03-07 16:18:38
Anhanguera
Sem viagens
Aricanduva
0 %  -  2023-03-07 16:18:54
20 %  -  2023-03-07 16:18:55
40 %  -  2023-03-07 16:18:55
60 %  -  2023-03-07 16:18:56
80 %  -  2023-03-07 16:18:56
Artur Alvim
0 %  -  2023-03-07 16:18:58
20 %  -  2023-03-07 16:19:00
40 %  -  2023-03-07 16:19:03
60 %  -  2023-03-07 16:19:05
80 %  -  2023-03-07 16:19:08
Barra Funda
0 %  -  2023-03-07 16:19:11
20 %  -  2023-03-07 16:19:15
40 %  -  2023-03-07 16:19:19
60 %  -  2023-03-07 16:19:23
80 %  -  2023-03-07 16:19:28
Bela Vista
0 %  -  2023-03-07 16:19:33
20 %  -  2023-03-07 16:19:36
40 %  -  2023-03-07 16:19:40
60 %  -  2023-03-07 16:19:44
80 %  -  2023-03-07 16:19:48
Belém
0 %  -  2023-03-07 16:19:52
20 % 

80 %  -  2023-03-07 16:44:19
Parelheiros
0 %  -  2023-03-07 16:44:38
20 %  -  2023-03-07 16:44:43
40 %  -  2023-03-07 16:44:48
60 %  -  2023-03-07 16:44:52
80 %  -  2023-03-07 16:44:57
Pari
0 %  -  2023-03-07 16:45:03
20 %  -  2023-03-07 16:45:06
40 %  -  2023-03-07 16:45:08
60 %  -  2023-03-07 16:45:10
80 %  -  2023-03-07 16:45:13
Parque do Carmo
0 %  -  2023-03-07 16:45:15
20 %  -  2023-03-07 16:45:17
40 %  -  2023-03-07 16:45:18
60 %  -  2023-03-07 16:45:19
80 %  -  2023-03-07 16:45:21
Pedreira
0 %  -  2023-03-07 16:45:23
20 %  -  2023-03-07 16:45:24
40 %  -  2023-03-07 16:45:25
60 %  -  2023-03-07 16:45:27
80 %  -  2023-03-07 16:45:28
Penha
0 %  -  2023-03-07 16:45:31
20 %  -  2023-03-07 16:45:36
40 %  -  2023-03-07 16:45:42
60 %  -  2023-03-07 16:45:47
80 %  -  2023-03-07 16:45:53
Perdizes
0 %  -  2023-03-07 16:45:59
20 %  -  2023-03-07 16:46:08
40 %  -  2023-03-07 16:46:16
60 %  -  2023-03-07 16:46:24
80 %  -  2023-03-07 16:46:33
Perus
Sem viagens
Pinheiros
0 %  -  2023-03-07 16:

ValueError: Cannot write empty DataFrame to file.